In [17]:
import json
import pandas as pd
import re
import requests
import numpy as np

In [18]:
with open("all_characters.json", "r") as read_file:
    data_other = json.load(read_file)
    
with open("cornell_movie_characters.json", "r") as read_file:
    data_cornell = json.load(read_file)

In [19]:
data_other

{'Anthony_Goldstein': {'name': 'Anthony Goldstein',
  'series': 'harry potter',
  'big_five': [0.7, 1.0, 0.25, -1.0, -0.22],
  'url': 'https://harrypotter.fandom.com/wiki/Anthony_Goldstein',
  'description': "Anthony Goldstein (b. 1980) was a half-blood wizard who began attending Hogwarts School of Witchcraft and Wizardry in 1991. He was Sorted into Ravenclaw house. In his fifth year he was selected as one of his House's prefects and joined Dumbledore's Army, an organisation taught and lead by Harry Potter. Anthony later fought beside fellow D.A. members in the Battle of Hogwarts the last battle of the Second Wizarding War.",
  'quote': ['Anthony: "Hiya, Harry. I heard you\'d found somewhere for the D.A. to meet."\nHarry Potter: "What!? This is supposed to be secret."\nAnthony: "It\'s all right. I heard it from Ernie, who heard it from Neville."\nHarry Potter: "We\'ll see you there then, yeah?"',
   "―Discussion of the D.A.'s meeting place"],
  'movie': ''},
 'Xenophilius_Lovegood': {'

In [20]:
char_name_list_other = list(data_other.keys())
char_name_list_cornell = list(data_cornell.keys())

In [21]:
intersected_script_reviews_other_franchise = pd.read_csv("intersected_script_reviews_other_franchise.csv")
intersected_script_reviews = pd.read_csv("intersected_script_reviews.csv")
intersected_script_reviews.head()

Unnamed: 0                                              link   category  \
0           0  http://www.imdb.com/title/tt0086190/usercomments  pos_train   
1           1  http://www.imdb.com/title/tt0086190/usercomments  pos_train   
2           2  http://www.imdb.com/title/tt0086190/usercomments  pos_train   
3           3  http://www.imdb.com/title/tt0086190/usercomments  pos_train   
4           4  http://www.imdb.com/title/tt0086190/usercomments  pos_train   

                                      review_content  rating    IMDB_ID  \
0  I couldn't have been more thrilled; Just eight...       9  tt0086190   
1  I suppose JEDI is now chronologically to be co...       8  tt0086190   
2  I know I know it was a good ending but sincere...      10  tt0086190   
3  As Most Off You Might off Seen Star Wars: Retu...      10  tt0086190   
4  No, there is another !<br /><br />Because ever...      10  tt0086190   

                                         Name  
0  Star Wars: Episode VI - Return of the Jedi  
1  Star Wars: Episode VI - Return of the Jedi  
2  Star Wars: Episode VI - Return of the Jedi  
3  Star Wars: Episode VI - Return of the Jedi  
4  Star Wars: Episode VI - Return of the Jedi

In [22]:
def get_series(name_in):
    if 'harry potter' in name_in.lower():
        return 'harry potter'
    elif 'game of thrones' in name_in.lower():
        return 'game of thrones'
    elif 'star wars' in name_in.lower():
        return 'star wars'
    
intersected_script_reviews_other_franchise['series'] = intersected_script_reviews_other_franchise['Name'].apply(get_series)

In [23]:
def remove_line_break(in_string):
    return in_string.replace("<br />", " ")
intersected_script_reviews_other_franchise["review_content"] = intersected_script_reviews_other_franchise["review_content"].apply(remove_line_break)
intersected_script_reviews["review_content"] = intersected_script_reviews["review_content"].apply(remove_line_break)

In [24]:
intersected_script_reviews_other_franchise.Name.unique()

array(['Star Wars: Episode 3: Revenge of the Sith',
       'Harry Potter and the Half-Blood Prince',
       'Star Wars: Episode 1: The Phantom Menace',
       'Star Wars: Episode 2: Attack of the Clones'], dtype=object)

In [25]:
intersected_script_reviews.Name.unique()

array(['Star Wars: Episode VI - Return of the Jedi', 'Moonstruck',
       'The Shining', 'Soldier', 'Mystery Men', 'Twelve Monkeys',
       'Halloween', 'Even Cowgirls Get the Blues', 'Man on Fire',
       'Kalifornia', 'Domino', 'Titanic', 'The Haunting', 'Birthday Girl',
       'Cliffhanger', 'Midnight Cowboy', 'Pet Sematary', 'Platoon',
       "Who's Your Daddy?", 'The Limey', 'Rush Hour 2', 'The Wedding Date',
       'Natural Born Killers', 'Rebel Without a Cause', 'The Lost Son',
       'Slither', 'Antitrust', 'Batman and Robin', 'The Mummy',
       'American Psycho', 'Magnolia',
       'A Nightmare on Elm Street 3: Dream Warriors',
       'Peggy Sue Got Married', 'Scary Movie 2', 'Tombstone', 'Zulu Dawn',
       'Freddy vs. Jason', 'Rambo: First Blood Part II', 'My Girl 2',
       'G.I. Jane', 'Apocalypse Now', 'Blade',
       'An American Werewolf in Paris', 'Black Snake Moan',
       '2001: A Space Odyssey', 'Nurse Betty', 'The Cell',
       'The English Patient', 'Never Been K

In [26]:
char_other_review_info = {}
for each in char_name_list_other:
    char_other_review_info[each] = {}
    char_other_review_info[each]["name_representation"] = data_other[each]['name'].split(" ")
    char_other_review_info[each]["review_count"] = 0
    char_other_review_info[each]["review_content"] = []
    char_other_review_info[each]["review_score"] = []
    char_other_review_info[each]["review_category"] = []
    char_other_review_info[each]["movie"] = data_other[each]["movie"]
    char_other_review_info[each]["series"] = data_other[each]["series"]
for each in char_name_list_other:
    char_other_review_info[each]["review_content"] = []

In [27]:
char_cornell_review_info = {}
for each in char_name_list_cornell:
    char_cornell_review_info[each] = {}
    char_cornell_review_info[each]["name_representation"] = data_cornell[each]['name'].split(" ")
    char_cornell_review_info[each]["review_count"] = 0
    char_cornell_review_info[each]["review_content"] = []
    char_cornell_review_info[each]["review_score"] = []
    char_cornell_review_info[each]["review_category"] = []
    char_cornell_review_info[each]["movie"] = data_cornell[each]["movie"]
    char_cornell_review_info[each]["series"] = data_cornell[each]["series"]
for each in char_name_list_cornell:
    char_cornell_review_info[each]["review_content"] = []

In [28]:
char_other_review_info

{'Anthony_Goldstein': {'name_representation': ['Anthony', 'Goldstein'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': '',
  'series': 'harry potter'},
 'Xenophilius_Lovegood': {'name_representation': ['Xenophilius', 'Lovegood'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': 'Harry Potter and the Deathly Hallows',
  'series': 'harry potter'},
 'Newt_Scamander': {'name_representation': ['Newt', 'Scamander'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': 'Fantastic Beasts and Where to Find Them ',
  'series': 'harry potter'},
 'Jacob_Kowalski': {'name_representation': ['Jacob', 'Kowalski'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': '',
  'series': 'harry potter'},
 'Katie_Bell': {'name_representation': ['Katie', 'Bell'],
  'review_count': 0,
  'review_content':

In [29]:
char_cornell_review_info

{'Richard_Reiben': {'name_representation': ['Richard', 'Reiben'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': 'Saving Private Ryan',
  'series': ''},
 'David': {'name_representation': ['David'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': 'Star Trek: The Wrath Of Khan',
  'series': ''},
 'Senator_Kelly': {'name_representation': ['Senator', 'Kelly'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': 'X-Men',
  'series': ''},
 'Superman': {'name_representation': ['Superman'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': 'Superman Iii',
  'series': ''},
 'Sal': {'name_representation': ['Sal'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': 'Do The Right Thing',
  'series': ''},
 'Aunt_May_(Rosemary_Harris)': 

In [30]:
# Some changes for other franchise
char_other_review_info['Barty_Crouch_Sr']["name_representation"] = ['Barty', 'Crouch']
char_other_review_info['Barty_Crouch_Jr']["name_representation"] = ['Barty', 'Crouch']
char_other_review_info['Bill_Weasley']["name_representation"] = ['Bill']
char_other_review_info['The_Fat_Friar']["name_representation"] = ['Friar']
char_other_review_info['Irma_Pince']["name_representation"] = ['Irma']
char_other_review_info['The_Waif']["name_representation"] = ['Waif']

# Some changes for cornell dataset
char_cornell_review_info['Dr._Doom_(Story_series)']["name_representation"] = ["Dr. Doom", "Dr Doom", 'Doctor Doom']
char_cornell_review_info['Professor_Barnhardt']["name_representation"] = ["Barnhardt"]
char_cornell_review_info['Dr._Lazarus']["name_representation"] = ["Lazarus"]
char_cornell_review_info['The_Wizard_Of_Oz_(person)']["name_representation"] = ["Wizard", "Oz"]
char_cornell_review_info["Buggin'_Out"]["name_representation"] = ["Buggin", "Bugging"]
char_cornell_review_info["Tin_Man"]["name_representation"] = ["Tin"]
char_cornell_review_info["Mr._Blonde"]["name_representation"] = ["Blonde"]
char_cornell_review_info["Tin_Man"]["name_representation"] = ["Tin"]
char_cornell_review_info["Tin_Man"]["name_representation"] = ["Tin"]
char_cornell_review_info["Tin_Man"]["name_representation"] = ["Tin"]
char_cornell_review_info["King_Edward_Longshanks"]["name_representation"] = ['King','Edward']
char_cornell_review_info["Baby_Herman"]["name_representation"] = ['Herman']
char_cornell_review_info["The_President"]["name_representation"] = ['President']
char_cornell_review_info["Invisible_Boy"]["name_representation"] = ['Invisible']
char_cornell_review_info['Mr._White']["name_representation"] = ["White"]
char_cornell_review_info['The_Man_with_All_the_Marbles']["name_representation"] = ["Marble", "Marbles"]
char_cornell_review_info['The_Joker']["name_representation"] = ["Joker"]
char_cornell_review_info['The_Wicked_Witch_Of_The_West']["name_representation"] = ["Witch"]
char_cornell_review_info['The_Joker']["name_representation"] = ["Joker"]
char_cornell_review_info['The_Joker']["name_representation"] = ["Joker"]
char_cornell_review_info['The_Joker']["name_representation"] = ["Joker"]
char_cornell_review_info['Mrs._Potato_Head']["name_representation"] = ["Potato"]


In [31]:
def give_regex_string(in_list):
    string_out = ""
    for i in range(len(in_list)):
        if i == len(in_list)-1:
            string_out += r"\b("+in_list[i].lower()+r")\b"
        else:
            string_out += r"\b("+in_list[i].lower()+r")\b|"
    return string_out

In [56]:
for each_char in char_other_review_info:
    for i in range(intersected_script_reviews_other_franchise.shape[0]):
        match_name = r"%s" % give_regex_string(char_other_review_info[each_char]['name_representation'])
        if (re.findall(match_name, intersected_script_reviews_other_franchise.iloc[i]['review_content'].lower()) != []) and char_other_review_info[each_char]["series"] == intersected_script_reviews_other_franchise.iloc[i]['series']: 
            char_other_review_info[each_char]['review_count'] += 1
            char_other_review_info[each_char]["review_content"].append(intersected_script_reviews_other_franchise.iloc[i]['review_content'])
            char_other_review_info[each_char]["review_score"].append(intersected_script_reviews_other_franchise.iloc[i]['rating'])
            char_other_review_info[each_char]["review_category"].append(intersected_script_reviews_other_franchise.iloc[i]['category'])
            
            
            

In [57]:
char_other_review_info

{'Anthony_Goldstein': {'name_representation': ['Anthony', 'Goldstein'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': '',
  'series': 'harry potter'},
 'Xenophilius_Lovegood': {'name_representation': ['Xenophilius', 'Lovegood'],
  'review_count': 4,
  'review_content': ['Oh god.  This movie butchered the magic of the book. I seriously wasn\'t sure if this was the same movie... Why didn\'t Dumbledore pick Harry up from the Dursleys and give them a piece of his mind? Where was the Slug Club? Why didn\'t Harry know that Sirius\' house was now his? not to mention Kreacher? It plays a big part in the next movies! Why weren\'t the lessons with Dumbledore fully developed? You find out almost NOTHING about Voldemort\'s past. Where were Bill and Fleur? Where was the twins\' shop? (Blink and you miss it) Where was Hagrid? Where was Neville? Where was Quiditch? Where was Tonks\' and Lupin\'s relationship??? What, am I just supposed to belie

In [58]:
for each_char in char_cornell_review_info:
    for i in range(intersected_script_reviews.shape[0]):
        match_name = r"%s" % give_regex_string(char_cornell_review_info[each_char]['name_representation'])
        if (re.findall(match_name, intersected_script_reviews.iloc[i]['review_content'].lower()) != []) and char_cornell_review_info[each_char]["movie"].lower() == intersected_script_reviews.iloc[i]['Name'].lower(): 
            char_cornell_review_info[each_char]['review_count'] += 1
            char_cornell_review_info[each_char]["review_content"].append(intersected_script_reviews.iloc[i]['review_content'])
            char_cornell_review_info[each_char]["review_score"].append(intersected_script_reviews.iloc[i]['rating'])
            char_cornell_review_info[each_char]["review_category"].append(intersected_script_reviews.iloc[i]['category'])
            
            
            

In [59]:
char_cornell_review_info

{'Richard_Reiben': {'name_representation': ['Richard', 'Reiben'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': 'Saving Private Ryan',
  'series': ''},
 'David': {'name_representation': ['David'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': 'Star Trek: The Wrath Of Khan',
  'series': ''},
 'Senator_Kelly': {'name_representation': ['Senator', 'Kelly'],
  'review_count': 0,
  'review_content': [],
  'review_score': [],
  'review_category': [],
  'movie': 'X-Men',
  'series': ''},
 'Superman': {'name_representation': ['Superman'],
  'review_count': 64,
  'review_content': ['The opening sequence to the film, kind of a Rube-Goldberg type slapstick thing which ends with a man almost getting drowned in his car, is a dead giveaway to the audience that this film is not going to be in the same league as the first two Supermans. It\'s supposed to be funny, but it just clunks along l

In [49]:
# for each in char_name_list_other:
#     char_other_review_info[each]['review_count'] = int(char_other_review_info[each]['review_count'])
#     if char_other_review_info[each]['review_score'] != []:
#         for each_score in char_other_review_info[each]['review_score']:
#             each_score = str(each_score)
#     char_other_review_info[each]['name_representation'] = list(char_other_review_info[each]['name_representation'])
#     char_other_review_info[each]['review_content'] = list(char_other_review_info[each]['review_content'])
#     char_other_review_info[each]['review_score'] = list(char_other_review_info[each]['review_score'])
#     char_other_review_info[each]['review_category'] = list(char_other_review_info[each]['review_category'])
# for each in char_name_list_cornell:
#     char_cornell_review_info[each]['review_count'] = int(char_cornell_review_info[each]['review_count'])
#     if char_cornell_review_info[each]['review_score'] != []:
#         for each_score in char_cornell_review_info[each]['review_score']:
#             each_score = int(each_score)
#     char_cornell_review_info[each]['name_representation'] = list(char_cornell_review_info[each]['name_representation'])
#     char_cornell_review_info[each]['review_content'] = list(char_cornell_review_info[each]['review_content'])
#     char_cornell_review_info[each]['review_score'] = list(char_cornell_review_info[each]['review_score'])
#     char_cornell_review_info[each]['review_category'] = list(char_cornell_review_info[each]['review_category'])
    

In [60]:
def default(o):
    if type(o) == np.int64: 
        return int(o)  
    raise TypeError

y = json.dumps(char_other_review_info, default=default)
with open('characters_review_other.json', 'w') as fp:
    json.dump(y, fp)

In [61]:
z = json.dumps(char_cornell_review_info, default=default)
with open('characters_review_cornell.json', 'w') as fp:
    json.dump(z, fp)

In [70]:
# Way to open:
with open("characters_review_other.json", "r") as read_file:
    dict_format = json.loads(json.load(read_file))

In [71]:
type(dict_format)

dict